In [93]:
{-# LANGUAGE TemplateHaskell #-}
{-# LANGUAGE FlexibleInstances #-}
{-# LANGUAGE FlexibleContexts #-}
{-# LANGUAGE RankNTypes #-}
{-# LANGUAGE ScopedTypeVariables #-}
{-# LANGUAGE TypeApplications #-}
{-# LANGUAGE TypeFamilies #-}
{-# LANGUAGE InstanceSigs #-}
{-# LANGUAGE OverloadedStrings #-}
{-# LANGUAGE AllowAmbiguousTypes #-}

import Control.Lens
import Numeric.Lens
import Data.Bits.Lens
import Data.Data.Lens

import Control.Applicative
import Data.Char as C
import qualified Data.Map as M
import qualified Data.Set as S
import qualified Data.Text as T
import qualified Data.List as L

Line 1: Unused LANGUAGE pragma
Found:
{-# LANGUAGE TemplateHaskell #-}
Why not:
Line 6: Unused LANGUAGE pragma
Found:
{-# LANGUAGE TypeApplications #-}
Why not:
Line 9: Unused LANGUAGE pragma
Found:
{-# LANGUAGE OverloadedStrings #-}
Why not:

In [9]:
-- both is a traversal which focuses both sides of a tuple if it has the same type in each side

-- Specialized to tuples
-- both :: Traversal (a, a) (b, b) a b

-- General
-- both :: Bitraversable r => Traversal (r a a) (r b b) a b

:t both

("Bubbles", "Buttercup") ^.. both

("Bubbles", "Buttercup") & both %~ (++ "!")

("Bubbles", "Buttercup") & both .~ "Blossom"

("Bubbles", "Buttercup") & both %~ length

(1, 2, 3) & each %~ (*10)

[1, 2, 3] & each %~ (*10)

("Here's Johnny" :: T.Text) & each %~ C.toUpper

("Houston we have a problem" :: T.Text) & each .~ (22 :: Int)

both :: forall (r :: * -> * -> *) (f :: * -> *) a b. (Bitraversable r, Applicative f) => (a -> f b) -> r a a -> f (r b b)

["Bubbles","Buttercup"]

("Bubbles!","Buttercup!")

("Blossom","Blossom")

(7,9)

(10,20,30)

[10,20,30]

"HERE'S JOHNNY"

: 

In [13]:
[1, 2, 3, 4, 5] & taking 3 traversed *~ 10

[1, 2, 3, 4, 5] & dropping 3 traversed *~ 10

-- focus characters until '-'
"once upon a time - optics became mainstream" & takingWhile (/= '-') traversed %~ toUpper

-- filter can be used to filter focuses from a traversal

-- Multiply all even numbers by 10
[1, 2, 3, 4, 5] & traversed . filtered even *~ 10

-- Reverse only the long strings
("short", "really long") & both . filtered ((> 5) . length) %~ reverse

[10,20,30,4,5]

[1,2,3,40,50]

"ONCE UPON A TIME - optics became mainstream"

[1,20,3,40,5]

("short","gnol yllaer")

### Traversal Combinators

In [23]:
-- Errors out
-- [1, 2, 3] & folded %~ (*10)

-- Simplified
-- traversed :: Traversable f => Traversal (f a) (f b) a b

-- A bit more complex
-- traversed :: Traversable f => IndexedTraversal Int (f a) (f b) a b

-- Actual
:t traversed

[1, 2, 3] & traversed *~ 10

-- Tuples are traversable over their last slot
("Batman", "Superman") & traversed %~ take 3

let powerLevels = M.fromList [ ("Gohan", 710), ("Goku", 9001), ("Krillin", 5000), ("Piccolo", 408) ]

powerLevels & traversed %~ \n -> if n > 9000 then "Over 9000" else show n

import Data.Tree

let opticsTree = Node "Lens" [Node "Fold" [], Node "Traversal" []]

opticsTree & traversed %~ reverse

traversed :: forall (p :: * -> * -> *) (f1 :: * -> *) (f2 :: * -> *) a b. (Indexable Int p, Traversable f1, Applicative f2) => p a (f2 b) -> f1 a -> f2 (f1 b)

[10,20,30]

("Batman","Sup")

fromList [("Gohan","710"),("Goku","Over 9000"),("Krillin","5000"),("Piccolo","408")]

Node {rootLabel = "sneL", subForest = [Node {rootLabel = "dloF", subForest = []},Node {rootLabel = "lasrevarT", subForest = []}]}

### More Combinators

In [30]:
-- worded :: Traversal' String String
-- lined  :: Traversal' String String

:t worded
:t lined

"I'll be back!" ^.. worded

"Run\nForrest\nRun" ^.. lined

-- Surround each word with '*'s
"blue suede shoes" & worded %~ \s -> "*" ++ s ++ "*"

-- Capitalize each word
"blue suede shoes" & worded %~ \(x:xs) -> C.toUpper x : xs

-- Add a "#" to the start of each line:
"blue\nsuede\nshoes" & lined %~ ('#':)

-- Mapping the identity function still has the
-- white-space collapsing side-effects of `unwords`
"blue \n suede \n \n shoes" & worded %~ id

worded :: forall (p :: * -> * -> *) (f :: * -> *). (Indexable Int p, Applicative f) => p String (f String) -> String -> f String

lined :: forall (p :: * -> * -> *) (f :: * -> *). (Indexable Int p, Applicative f) => p String (f String) -> String -> f String

["I'll","be","back!"]

["Run","Forrest","Run"]

"*blue* *suede* *shoes*"

"Blue Suede Shoes"

"#blue\n#suede\n#shoes"

"blue suede shoes"

### Traversing multiple paths at once

In [42]:
-- beside :: Traversal s t a b -> Traversal s' t' a b -> Traversal (s, s') (t, t') a b

-- beside :: Lens s t a b -> Lens s' t' a b -> Traversal (s, s') (t, t') a b
-- beside :: Fold s a     -> Fold s' a      -> Fold (s, s') a

let dinos = ("T-Rex", (42, "Stegosaurus"))

dinos ^.. beside id _2

let numbers = ([(1, 2), (3, 4)], [5, 6, 7])

numbers ^.. beside (traversed . both) traversed

("T-Rex", ("Ankylosaurus", "Stegosaurus")) ^.. beside id both

-- both = beside id id

-- We can modify all characters inside both halves of the tuple
("Cowabunga", ["let's", "order", "pizza"])
    -- Each half of the tuple has a different path to focus the characters
    & beside traversed (traversed . traversed)
    %~ toUpper
    
-- beside both traversed :: Traversal' (Either (Int, Int) [Int]) Int
Left (1, 2) & beside both traversed %~ negate

Right [3, 4] & beside both traversed %~ negate :: Either (Int, Int) [Int]

["T-Rex","Stegosaurus"]

[1,2,3,4,5,6,7]

["T-Rex","Ankylosaurus","Stegosaurus"]

("COWABUNGA",["LET'S","ORDER","PIZZA"])

Left (-1,-2)

Right [-3,-4]

### Focusing a specific traversal element

In [44]:
-- element :: Traversable f => Int -> Traversal' (f a) a

:t element

[0, 1, 2, 3, 4] ^? element 2

[0, 1, 2, 3, 4] & element 2 *~ 100

-- elementOf :: Traversal' s a -> Int -> Traversal' s a
-- elementOf :: Fold s a       -> Int -> Fold s a

-- `element` is basically `elementOf traversed`
[0, 1, 2, 3, 4] ^? elementOf traversed 2

-- We can get a specific element from a composition of traversals
[[0, 1, 2], [3, 4], [5, 6, 7, 8]] ^? elementOf (traversed . traversed) 6

-- Modify the 6th integer from within nested lists:
[[0, 1, 2], [3, 4], [5, 6, 7, 8]]
    & elementOf (traversed . traversed) 6 *~ 100

element :: forall (p :: * -> * -> *) (t :: * -> *) (f :: * -> *) a. (Indexable Int p, Traversable t, Applicative f) => Int -> p a (f a) -> t a -> f (t a)

Just 2

[0,1,200,3,4]

### Composing Traversals

In [47]:
-- Capitalize the first char of every word
"blue suede shoes" & worded . taking 1 traversed %~ toUpper

-- Find all strings longer than 5 chars
-- then surround each word in that string with '*'
["short", "really long"]
    & traversed
    . filtered ((> 5) . length)
    . worded
    %~ \s -> "*" ++ s ++ "*"
    
-- Add "Rich " to the names of people with more than $1000
(("Ritchie", 100000), ("Archie", 32), ("Reggie", 4350))
    & each
    . filtered ((> 1000) . snd)
    . _1
    %~ ("Rich " ++)

"Blue Suede Shoes"

["short","*really* *long*"]

(("Rich Ritchie",100000),("Archie",32),("Rich Reggie",4350))

### Exercises - Simple Traversals

In [67]:
-- 1.

-- What type of optic do you get when you compose a traversal with a fold?
-- We get a fold

-- Which of the optics we have learned can act as a traversal?
-- Lens or Traversal

-- Which of the optics we have learned can act as a fold?
-- Lens, traversal and fold

-- 2.
-- Fill in the blank to complete each expression:

("Jurassic", "Park") & each .~ "N/A"

("Jurassic", "Park") & both . traversed .~ 'x'

("Malcolm", ["Kaylee", "Inara", "Jayne"])
    & beside id traversed %~ take 3

("Malcolm", ["Kaylee", "Inara", "Jayne"])
    & _2 . element 1 .~ "River"

["Die Another Day", "Live and Let Die", "You Only Live Twice"]
    & traversed . elementOf worded 1 . traversed .~ 'x'

:t each
:t traversed

((True, "Strawberries"), (False, "Blueberries"), (True, "Blackberries")) 
    & each . filtered fst . _2 . taking 5 traversed %~ C.toUpper
    
((True, "Strawberries"), (False, "Blueberries"), (True, "Blackberries"))
    & each %~ snd

("N/A","N/A")

("xxxxxxxx","xxxx")

("Mal",["Kay","Ina","Jay"])

("Malcolm",["Kaylee","River","Jayne"])

["Die xxxxxxx Day","Live xxx Let Die","You xxxx Live Twice"]

each :: forall s t a b (f :: * -> *). (Each s t a b, Applicative f) => (a -> f b) -> s -> f t

traversed :: forall (p :: * -> * -> *) (f1 :: * -> *) (f2 :: * -> *) a b. (Indexable Int p, Traversable f1, Applicative f2) => p a (f2 b) -> f1 a -> f2 (f1 b)

((True,"STRAWberries"),(False,"Blueberries"),(True,"BLACKberries"))

("Strawberries","Blueberries","Blackberries")

### Traversal Actions

In [75]:
:t sequenceA


sequenceA [Just 1, Just 2, Just 3]

sequenceA [Just 1, Nothing, Just 3]

sequenceA $ Just (Left "Whoops")

sequenceA ([pure 1, pure 2, pure 3] :: [IO Int]) >>= print

:t traverse

import Text.Read (readMaybe)

:t readMaybe

traverse readMaybe ["1", "2", "3"] :: Maybe [Int]

traverse readMaybe ["1", "snark", "3"] :: Maybe [Int]

:t readFile

let results = traverse readFile ["file1.txt", "file2.txt"]

:t results

traverse (\n -> [n * 10, n * 100]) ("a", 10)

sequenceA :: forall (t :: * -> *) (f :: * -> *) a. (Traversable t, Applicative f) => t (f a) -> f (t a)

Just [1,2,3]

Nothing

Left "Whoops"

[1,2,3]

...

Just [1,2,3]

Nothing

readFile :: FilePath -> IO String

results :: IO [String]

[("a",100),("a",1000)]

### Traverse on Traversals

In [81]:
-- Specialized signature
-- traverseOf :: Traversal s t a b -> (a -> f b) -> s -> f t

-- Real signature
-- traverseOf :: LensLike f s t a b -> (a -> f b) -> s -> f t

:t traverse
:t traverseOf
:t traverseOf traversed

traverseOf both readMaybe ("1", "2") :: Maybe (Int, Int)

traverseOf both readMaybe ("not a number", "2") :: Maybe (Int, Int)

traverseOf both (\c -> [toLower c, toUpper c]) ('a', 'b')

traverseOf
    (both . traversed)
    (\c -> [toLower c, toUpper c])
    ("ab", "cd")

traverse :: forall (t :: * -> *) (f :: * -> *) a b. (Traversable t, Applicative f) => (a -> f b) -> t a -> f (t b)

traverseOf :: forall (f :: * -> *) s t a b. LensLike f s t a b -> (a -> f b) -> s -> f t

traverseOf traversed :: forall (f1 :: * -> *) (f2 :: * -> *) a b. (Traversable f1, Applicative f2) => (a -> f2 b) -> f1 a -> f2 (f1 b)

Just (1,2)

Nothing

[('a','b'),('a','B'),('A','b'),('A','B')]

[("ab","cd"),("ab","cD"),("ab","Cd"),("ab","CD"),("aB","cd"),("aB","cD"),("aB","Cd"),("aB","CD"),("Ab","cd"),("Ab","cD"),("Ab","Cd"),("Ab","CD"),("AB","cd"),("AB","cD"),("AB","Cd"),("AB","CD")]

In [88]:
validateEmail :: String -> Either String String
validateEmail email | elem '@' email = Right email
                    | otherwise      = Left ("missing '@': " <> email)
                    
traverseOf (traversed . _2) validateEmail
    [ ("Mike", "mike@tmnt.io")
    , ("Raph", "raph@tmnt.io")
    , ("Don", "don@tmnt.io")
    , ("Leo", "leo@tmnt.io")
    ]
    
traverseOf (traversed . _2) validateEmail
    [ ("Mike", "mike@tmnt.io")
    , ("Raph", "raph.io")
    , ("Don", "don@tmnt.io")
    , ("Leo", "leo@tmnt.io")
    ]
    
-- forOf :: Traversal s t a b -> s -> (a -> f b) -> f t
:t forOf

-- sequenceAOf :: Traversal s t (f a) a -> s -> f t
:t sequenceAOf

sequenceAOf _1 (Just "Garfield", "Lasagna")

sequenceAOf _1 (Nothing, "Lasagna")

sequenceAOf (both . traversed) ([Just "apples"], [Just "oranges"])

sequenceAOf (both . traversed) ([Just "apples"], [Nothing])

Right [("Mike","mike@tmnt.io"),("Raph","raph@tmnt.io"),("Don","don@tmnt.io"),("Leo","leo@tmnt.io")]

Left "missing '@': raph.io"

forOf :: forall (f :: * -> *) s t a b. LensLike f s t a b -> s -> (a -> f b) -> f t

sequenceAOf :: forall (f :: * -> *) s t b. LensLike f s t (f b) b -> s -> f t

Just ("Garfield","Lasagna")

Nothing

Just (["apples"],["oranges"])

Nothing

In [ ]:
-- traverseOf :: Traversal s t a b -> (a -> f b) -> s -> f t
-- (%%~)      :: Traversal s t a b -> (a -> f b) -> s -> f t

(("1", "2") & both %%~ readMaybe) :: Maybe (Int, Int)

(("not a number", "2") & both %%~ readMaybe) :: Maybe (Int, Int)

### Exercises - Traversal Actions

In [98]:
sequenceAOf _1 (Nothing, "Rosebug")

-- sequenceAOf (traversed . _1) [("ab", 1), ("cd", 2)]

sequenceAOf traversed [ZipList [1, 2], ZipList [3, 4]]

sequenceAOf (traversed . _2) [('a', ZipList [1, 2]), ('b', ZipList [3, 4])]

import Control.Monad.State
let result = traverseOf (beside traversed both) (\n -> modify (+n) >> get) ([1, 1, 1], (1, 1))
runState result 0

Nothing

ZipList {getZipList = [[1,3],[2,4]]}

ZipList {getZipList = [[('a',1),('b',3)],[('a',2),('b',4)]]}

(([1,2,3],(4,5)),5)

### Custom Traversals

In [104]:
-- values :: Traversal [a] [b] a b

-- values :: Applicative f => (a -> f b) -> [a] -> f [b]

values :: Applicative f => (a -> f b) -> [a] -> f [b]
values _ [] = pure []
values handler (a : as) = liftA2 (:) (handler a) (values handler as)

data Transaction =
    Withdrawal { _amount :: Int }
  | Deposit    { _amount :: Int }
  deriving Show
  
makeLenses ''Transaction

newtype BankAccount =
    BankAccount
    { _transactions :: [Transaction]
    } deriving Show
makeLenses ''BankAccount

let aliceAccount = BankAccount [Deposit 100, Withdrawal 20, Withdrawal 10]

aliceAccount ^.. transactions . traversed

aliceAccount ^.. transactions . traversed . amount

-- deposits :: Traversal' [Transaction] Int
-- deposits :: Traversal [Transaction] [Transaction] Int Int
deposits :: Applicative f => (Int -> f Int) -> [Transaction] -> f [Transaction]
deposits _ [] = pure []
deposits handler (Withdrawal amt : rest) =
    liftA2 (:) (pure (Withdrawal amt)) (deposits handler rest)
deposits handler (Deposit amt : rest) =
    liftA2 (:) (Deposit <$> (handler amt)) (deposits handler rest)
    
[Deposit 10, Withdrawal 20, Deposit 30] ^.. deposits

[Deposit 10, Withdrawal 20, Deposit 30] & deposits *~ 10

[Deposit {_amount = 100},Withdrawal {_amount = 20},Withdrawal {_amount = 10}]

[100,20,10]

[10,30]

[Deposit {_amount = 100},Withdrawal {_amount = 20},Deposit {_amount = 300}]

### Exercises - Custom Traversals

In [105]:
amountT :: Traversal' Transaction Int
amountT handler (Deposit n) = Deposit <$> handler n
amountT handler (Withdrawal n) = Withdrawal <$> handler n

myBoth :: Traversal (a, a) (b, b) a b
myBoth handler (a, a') = liftA2 (,) (handler a) (handler a')

transactionDelta :: Traversal' Transaction Int
transactionDelta handler (Deposit n) = Deposit <$> handler n
transactionDelta handler (Withdrawal n) = Withdrawal . negate <$> handler (negate n)

left :: Traversal (Either a b) (Either a' b) a a'
left f (Left a) = Left <$> f a
left _ (Right b) = pure (Right b)

beside :: Traversal s t a b -> Traversal s' t' a b -> Traversal (s,s') (t,t') a b
beside left' right' handler (s, s') = liftA2 (,) (s & left' %%~ handler) (s' & right' %%~ handler)

In [113]:
-- partsOf :: Traversal' s a -> Lens' s [a]
:t partsOf

[('a', 1), ('b', 2), ('c', 3)] ^. partsOf (traversed . _1)
[('a', 1), ('b', 2), ('c', 3)] ^. partsOf (traversed . _2)

[('a', 1), ('b', 2), ('c', 3)]
    & partsOf (traversed . _1) .~ ['c', 'a', 't']
    
-- Any 'extra' list elements are simply ignored
[('a', 1), ('b', 2), ('c', 3)]
    & partsOf (traversed . _1) .~ ['l', 'e', 'o', 'p', 'a', 'r', 'd']
    
-- Providing too few elements will keep the originals
[('a', 1), ('b', 2), ('c', 3)]
    & partsOf (traversed . _1) .~ ['x']
    
[('a', 1), ('b', 2), ('c', 3)]
    & partsOf (traversed . _1) %~ reverse
    
[('o', 1), ('o', 2), ('f', 3)]
    & partsOf (traversed . _1) %~ L.sort
    
[('o', 1), ('o', 2), ('f', 3)]
    & partsOf (traversed . _1) %~ tail

("how is a raven ", "like a ", "writing desk")
    & partsOf (each . traversed) %~ unwords . L.sort . words

partsOf :: forall (f :: * -> *) s t a. Functor f => Traversing (->) f s t a a -> LensLike f s t [a] [a]

"abc"

[1,2,3]

[('c',1),('a',2),('t',3)]

[('l',1),('e',2),('o',3)]

[('x',1),('b',2),('c',3)]

[('c',1),('b',2),('a',3)]

[('f',1),('o',2),('o',3)]

[('o',1),('f',2),('f',3)]

("a a desk how is"," like r","aven writing")